In [29]:
import pandas
import numpy
import requests
import folium
from folium.plugins import Draw
from shapely.geometry import Point, Polygon
from shapely.geometry import Polygon, MultiPolygon
from folium.features import GeoJson, GeoJsonPopup
from branca.colormap import linear
import h3
from shapely.ops import transform
from functools import partial
import pyproj
import xml.etree.ElementTree as ET
from svgpathtools import parse_path,CubicBezier, Line
import math
from pyproj import Proj
import branca.colormap as cm
import matplotlib.cm as mpl_cm

api_url = "https://nominatim.openstreetmap.org/search.php?q=Leipzig+Germany&polygon_geojson=1&format=json"
response = requests.get(api_url)
geo_coordinates = response.json()
leipzig_box = geo_coordinates[0].get('boundingbox')
leipzig_box = numpy.array(leipzig_box, dtype=numpy.float64)
bounding_box = (leipzig_box[0], leipzig_box[1],leipzig_box[2], leipzig_box[3])

bounding_box = (leipzig_box[0], leipzig_box[1],leipzig_box[2], leipzig_box[3])
mobile_metrics_df = pandas.read_csv('C://Users//trist//OneDrive//Desktop//The_Holy_Grail//mobile_metrics_df.csv')
mobile_metrics_df.rename(columns={'lte_rssnr': 'rssnr', 'level': 'rsrp', 'lte_cqi': 'cqi'}, inplace=True)

In [2]:
file0 = pandas.read_csv('C://Users//trist//5GNewRadioProject//MobileRadioFiles//spatial_humanities//Unfallorte2016_LinRef.csv',sep=";")
file1 = pandas.read_csv('C://Users//trist//5GNewRadioProject//MobileRadioFiles//spatial_humanities//Unfallorte2017_LinRef.csv',sep = ";")
file2 = pandas.read_csv('C://Users//trist//5GNewRadioProject//MobileRadioFiles//spatial_humanities//Unfallorte2018_LinRef.csv',sep = ";")
file3 = pandas.read_csv('C://Users//trist//5GNewRadioProject//MobileRadioFiles//spatial_humanities//Unfallorte2019_LinRef.csv',sep = ";")
file4 = pandas.read_csv('C://Users//trist//5GNewRadioProject//MobileRadioFiles//spatial_humanities//Unfallorte2020_LinRef.csv',sep = ";")
file5 = pandas.read_csv('C://Users//trist//5GNewRadioProject//MobileRadioFiles//spatial_humanities//Unfallorte2021_LinRef.csv',sep = ";")
dataframe_list = [file1,file2,file3,file4,file5]

C:\Users\trist\AppData\Local\Temp\ipykernel_18912\2545726259.py:2: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  file1 = pandas.read_csv('C://Users//trist//5GNewRadioProject//MobileRadioFiles//spatial_humanities//Unfallorte2017_LinRef.csv',sep = ";")
C:\Users\trist\AppData\Local\Temp\ipykernel_18912\2545726259.py:6: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  file5 = pandas.read_csv('C://Users//trist//5GNewRadioProject//MobileRadioFiles//spatial_humanities//Unfallorte2021_LinRef.csv',sep = ";")


In [13]:
complete_dataframe = file0
for dataframe in dataframe_list:
    complete_dataframe = pandas.concat([complete_dataframe,dataframe],ignore_index=True)

def utm_to_latlon(easting, northing, zone_number, zone_letter):
    utm_proj = Proj(proj='utm', zone=zone_number, ellps='WGS84', north=True)
    lon, lat = utm_proj(easting, northing, inverse=True)
    return lon,lat

dataframe['lat'] = dataframe['LINREFY'].map(lambda lat: lat.replace(',', '.'))
dataframe['lon'] = dataframe['LINREFX'].map(lambda lon: lon.replace(',', '.'))
for i in range(dataframe.shape[0]):
    lon,lat = utm_to_latlon(dataframe['lon'].iloc[i],dataframe['lat'].iloc[i],32,'N')
    dataframe.loc[i,'lon'] = lon
    dataframe.loc[i,'lat'] = lat


In [14]:
def get_dataframe_within_range(data_frame: pandas.DataFrame,range_lat,range_lon):
    index = numpy.where((data_frame["lon"] > range_lon[0]) & (data_frame["lon"] < range_lon[1])
                         & (data_frame["lat"] > range_lat[0]) & (data_frame["lat"] < range_lat[1]))
    index = numpy.array(index)
    index = index.ravel()
    index = index.tolist()
    index = data_frame.index[index]
    return data_frame.loc[index]

dataframe = get_dataframe_within_range(dataframe,[leipzig_box[0],leipzig_box[1]],[leipzig_box[2],leipzig_box[3]])
dataframe

OBJECTID           UIDENTSTLAE  ULAND  UREGBEZ  UKREIS  UGEMEINDE  \
120655    120656  14210301144200177310     14        7      13          0   
120657    120658  14210517148310364090     14        7      13          0   
120658    120659  14210503144200327430     14        7      13          0   
120673    120674  14210317144200213210     14        7      13          0   
120685    120686  14210103148310089390     14        7      13          0   
...          ...                   ...    ...      ...     ...        ...   
228538    228539  14211023144200806520     14        7      13          0   
228542    228543  14211130144200912290     14        7      13          0   
228543    228544  14211120148210890620     14        7      13          0   
228551    228552  14211015148210807231     14        7      13          0   
228553    228554  14211103144200834320     14        7      13          0   

        UJAHR  UMONAT  USTUNDE  UWOCHENTAG  ...  IstFuss  IstKrad  IstGkfz  \
120655   2021       3       16           2  ...        0        0        0   
120657   2021       5       17           2  ...        0        0        0   
120658   2021       5        6           2  ...        0        0        0   
120673   2021       3        5           4  ...        0        0        0   
120685   2021       1       14           1  ...        0        0        0   
...       ...     ...      ...         ...  ...      ...      ...      ...   
228538   2021      10        1           7  ...        0        0        0   
228542   2021      11        8           3  ...        0        1        0   
228543   2021      11       13           7  ...        0        0        0   
228551   2021      10       10           6  ...        0        0        0   
228553   2021      11       15           4  ...        0        0        0   

        IstSonstige                 LINREFX                  LINREFY  \
120655            0  741730,353001618757844  5687493,833982555195689   
120657            0  728898,827185031026602  5691758,867874955758452   
120658            0  732792,939088235609233  5696858,846367839723825   
120673            0  743389,712073598057032  5695196,003962710499763   
120685            0  727161,093606192618608  5689338,927991315722466   
...             ...                     ...                      ...   
228538            0  735263,162770261056721  5689590,202051261439919   
228542            0  734785,076948286965489  5689832,105579195544124   
228543            0  735003,547565030865371  5691834,906558433547616   
228551            1  736706,545001532882452  5689657,495985157787800   
228553            1  731773,866887103766203  5692342,636446377262473   

                 XGCSWGS84           YGCSWGS84        lat        lon  
120655  12,466861700000038  51,287386833000028  51.287387  12.466862  
120657  12,285903750000045  51,330975495000075  51.330975  12.285904  
120658  12,345039324000027  51,375175824000053  51.375176  12.345039  
120673  12,495870284000034  51,355809500000078  51.355809   12.49587  
120685  12,259459888000038  51,309947283000042  51.309947   12.25946  
...                    ...                 ...        ...        ...  
228538  12,375666679000062  51,308912170000042  51.308912  12.375667  
228542  12,368978808000065  51,311280986000043  51.311281  12.368979  
228543  12,373427837000065  51,329168805000052  51.329169  12.373428  
228551  12,396382717000051  51,308917889000043  51.308918  12.396383  
228553  12,327481199000033  51,335051685000053  51.335052  12.327481  

[1745 rows x 27 columns]

In [56]:
def create_hex_grid(bbox, resolution):
    min_lon, min_lat, max_lon, max_lat = bbox[2],bbox[0],bbox[3],bbox[1]
    hexagons = h3.polyfill_polygon([[min_lon, min_lat], [max_lon, min_lat], [max_lon, max_lat], [min_lon, max_lat]],
                                   resolution)
    cell_data = []

    for hexagon in hexagons:
        center_lat, center_lon = h3.h3_to_geo(hexagon)
        hexagon_polygon = h3.h3_to_geo_boundary(hexagon)
        insert_value_here = None

        cell_info = {
            'hex_id': h3.geo_to_h3(center_lat, center_lon, resolution),
            'center': (center_lat, center_lon),
            'hexagon_vertices': hexagon_polygon,
            'rsrp': insert_value_here,
            'rssi': insert_value_here,
            'rssnr': insert_value_here,
            'cqi': insert_value_here,
        }

        cell_data.append(cell_info)

    cell_df = pandas.DataFrame(cell_data)
    return cell_df

def visualize_hex_grid(cell_data, feature_label, map, layer_name):
    cell_data[feature_label] = cell_data[feature_label].astype(float)
    colormap = cm.LinearColormap(
        colors=mpl_cm.viridis.colors,
        vmin=cell_data[feature_label].min(),
        vmax=cell_data[feature_label].max()
    )
    colormap.caption = feature_label
    colormap.add_to(map)

    feature_group = folium.FeatureGroup(name=layer_name)

    for _, row in cell_data.iterrows():
        hex_id = row['hex_id']
        hexagon_vertices = row['hexagon_vertices']
        value = row[feature_label]

        feature = {
            'type': 'Feature',
            'geometry': {
                'type': 'Polygon',
                'coordinates': [h3.h3_to_geo_boundary(hex_id, geo_json=True)]
            },
            'properties': {
                feature_label: value,
                'hex_id': hex_id
            }
        }

        geojson = folium.GeoJson(
            data=feature,
            style_function=lambda x: {
                'fillColor': colormap(x['properties'][feature_label]),
                'fillOpacity': 0.4,
                'color': 'black',
                'weight': 1
            },
            highlight_function=lambda x: {'fillOpacity': 0.9}
        )

        popup = folium.GeoJsonPopup(fields=[feature_label, 'hex_id'], labels=True)
        popup.add_to(geojson)
        geojson.add_to(feature_group)

    feature_group.add_to(map)

def add_points_continuos(dataframe, feature_label, map, layer_name, radius=15):
    feature_group = folium.FeatureGroup(name=layer_name)
    colormap = linear.YlOrRd_09.scale(min(dataframe[feature_label]), max(dataframe[feature_label]))

    for _, point_info in dataframe.iterrows():
        lat = point_info['lat']
        lon = point_info['lon']
        value = point_info[feature_label]

        folium.Circle(
            location=[lat, lon],
            radius=radius,
            color=colormap(value),
            fill=True,
            fill_color=colormap(value),
            fill_opacity=0.7,
            popup=folium.Popup(f'{feature_label}: {value}', max_width=250)
        ).add_to(feature_group)

    feature_group.add_to(map)

def add_points(dataframe, map, layer_name, color ='black', radius=15):
    feature_group = folium.FeatureGroup(name=layer_name)

    for _, point_info in dataframe.iterrows():
        lat = point_info['lat']
        lon = point_info['lon']

        folium.Circle(
            location=[lat, lon],
            radius=radius,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7,
            popup=folium.Popup(f'Location: {(lat,lon)}', max_width=250)
        ).add_to(feature_group)

    feature_group.add_to(map)

def assign_hexid(dataframe:pandas.DataFrame,resolution = 8):
    hexID_map = []
    dataframe[['lat','lon']] = dataframe[['lat','lon']].apply(pandas.to_numeric)
    for index,row in dataframe.iterrows():
        hexID_map.append(h3.geo_to_h3(row.lat,row.lon,resolution))
    dataframe['hex_id'] = hexID_map
    return dataframe

def assign_building_to_cell(building_data, cell_data, resolution):
    building_data['hex_id'] = ""
    building_data['error_message'] = ""

    for index, building_row in building_data.iterrows():
        try:
            building_geometry = building_row['geometry']
            hex_id = ""

            if isinstance(building_geometry, Point):
                # If building is a single point, find the containing hexagon cell
                lat, lon = building_geometry.y, building_geometry.x
                hex_id = h3.geo_to_h3(lat, lon, resolution)
            elif isinstance(building_geometry, Polygon):
                # If building is a polygon, find the intersecting hexagon cells
                for cell_info in cell_data:
                    cell_polygon = Polygon(cell_info['hexagon_vertices'])
                    if building_geometry.intersects(cell_polygon):
                        hex_id = cell_info['hex_id']
                        break
            elif isinstance(building_geometry, MultiPolygon):
                # If building is a multipolygon, find the intersecting hexagon cells for each polygon
                for polygon in building_geometry:
                    for cell_info in cell_data:
                        cell_polygon = Polygon(cell_info['hexagon_vertices'])
                        if polygon.intersects(cell_polygon):
                            hex_id = cell_info['hex_id']
                            break
                    if hex_id:
                        break
            building_data.at[index, 'hex_id'] = hex_id

        except Exception as e:
            error_message = f"Error occurred for building at index {index}: {str(e)}"
            print(error_message)
            building_data.at[index, 'hex_id'] = ""
            building_data.at[index, 'error_message'] = error_message

    return building_data

def create_cell_info(dataframe,features = [],resolution = 8):
    unique_hex_id = dataframe['hex_id'].unique()
    cell_data = []
    for hex_id in unique_hex_id:
        center_lat, center_lon = h3.h3_to_geo(hex_id)
        hexagon_polygon = h3.h3_to_geo_boundary(hex_id)
        subframe = dataframe.loc[dataframe['hex_id'] == hex_id]
        cell_info = {'hex_id':hex_id, 'center': (center_lat, center_lon),'hexagon_vertices': hexagon_polygon,'area': h3.hex_area(resolution, unit='m^2'),'measurement_density': subframe.shape[0]}
        for feature in features:
            cell_info[feature] = subframe[feature].mean()
        cell_data.append(cell_info)
    return pandas.DataFrame(cell_data)

In [ ]:
import numpy as np
import tensorflow as tf
from tensorflow import keras

layer_sizes = [64]

X = mobile_metrics_df[['rssnr', 'cqi', 'rsrp', 'lon', 'lat']].values

y = mobile_metrics_df['rsrp'].values

model = keras.Sequential()
model.add(keras.layers.Dense(layer_sizes[0], activation='relu', input_shape=(X.shape[1],)))

for layer_size in layer_sizes[1:]:
    model.add(keras.layers.Dense(layer_size, activation='relu'))

model.add(keras.layers.Dense(1))

split_ratio = 0.2
split_index = int(X.shape[0] * (1 - split_ratio))
X_train, X_test = X[:split_index], X[split_index:]
y_train, y_test = y[:split_index], y[split_index:]

optimizer = 'adam'
model.compile(optimizer=optimizer, loss='mean_squared_error')
model.fit(X_train, y_train, epochs=15, batch_size=32)

loss = model.evaluate(X_test, y_test)
print('Mean Squared Error:', loss)

y_pred = model.predict(X_test)

input_predictions = model.predict(X_test)

The following section is just a test for my hexagonal grids and can be ignored

In [60]:
car_subframe = dataframe.loc[dataframe['IstPKW'] == 1]
bike_subframe = dataframe.loc[dataframe['IstRad'] == 1]
foot_subframe = dataframe.loc[dataframe['IstFuss'] == 1]
sonstige_subframe = dataframe.loc[dataframe['IstSonstige'] == 1]

In [ ]:
accidents_df = assign_hexid(dataframe,resolution =8)
accidents_cellinfo = create_cell_info(accidents_df,resolution = 8)

mm_df = assign_hexid(mobile_metrics_df,resolution = 8)
mm_cellinfo = create_cell_info(mm_df,['rsrp','cqi','rssnr'])


In [49]:
accidents_cellinfo
mm_cellinfo

hex_id                                    center  \
0    881f1ab92dfffff    (51.33271308335739, 12.42123636032252)   
1    881f1a164bfffff    (51.33192822279375, 12.37404763598671)   
2    881f1ab913fffff  (51.350479726512496, 12.496817055146273)   
3    881f1a10dbfffff   (51.25482935748902, 12.276529549256104)   
4    881f1a8c4dfffff    (51.39026825027962, 12.24196183371796)   
..               ...                                       ...   
499  881f1a1291fffff    (51.2840484887125, 12.263971409950935)   
500  881f1abb13fffff  (51.401590725014756, 12.474947714172753)   
501  881f1a8e3dfffff  (51.408916071921226, 12.257696231826511)   
502  881f1ab803fffff   (51.38773871018411, 12.528446455676006)   
503  881f1a8e8bfffff    (51.4178642135811, 12.349004698953381)   

                                      hexagon_vertices      area  \
0    ((51.335691515060745, 12.41599993376382), (51....  737327.6   
1    ((51.33490431871246, 12.368810196476142), (51....  737327.6   
2    ((51.35346100841631, 12.491581010538521), (51....  737327.6   
3    ((51.25780467811638, 12.271295758961292), (51....  737327.6   
4    ((51.39323454147101, 12.236716985538122), (51....  737327.6   
..                                                 ...       ...   
499  ((51.28702160615032, 12.258735125279241), (51....  737327.6   
500  ((51.40456815461222, 12.469707282017591), (51....  737327.6   
501  ((51.41188215273414, 12.252450314590176), (51....  737327.6   
502  ((51.39071957851116, 12.523208309566138), (51....  737327.6   
503  ((51.42083441973615, 12.343760155493769), (51....  737327.6   

     measurement_density        rsrp        cqi      rssnr  
0                   1183 -103.771767   6.292477  11.382925  
1                   4505  -94.979800   9.716093   1.840178  
2                    230  -94.026087  10.069565   3.391304  
3                    442  -99.289593   9.678733   1.230769  
4                    502 -104.262948   8.966135   0.284861  
..                   ...         ...        ...        ...  
499                    8  -98.125000  12.750000   5.625000  
500                    7  -95.571429  10.428571   7.285714  
501                    1 -107.000000   4.000000   0.000000  
502                    5 -107.400000   5.800000   0.000000  
503                    1  -77.000000  13.000000   0.000000  

[504 rows x 8 columns]

In [65]:
map = folium.Map(location=[51.3397,12.3731], zoom_start=12, tiles = 'cartodbpositron')

In [66]:
visualize_hex_grid(accidents_cellinfo,'measurement_density',map,'Accident_Clusters')
visualize_hex_grid(mm_cellinfo,'rsrp',map,'Empirical_RSRP')
add_points(car_subframe,map,'Car_accidents',color = 'red')
add_points(bike_subframe,map,'Bike_accidents',color = 'blue')
add_points(foot_subframe,map,'Foot_accidents',color = 'green')
add_points(sonstige_subframe,map,'Otherwise',color = 'orange')


In [67]:
folium.LayerControl().add_to(map)
map